# Performance tips

In [1]:
using DataFrames
using BenchmarkTools
using CategoricalArrays
using PooledArrays
using Random

## Access by column number is faster than by name

In [2]:
x = DataFrame(rand(5, 1000), :auto)
@btime $x[!, 500]; ## Faster

  3.095 ns (0 allocations: 0 bytes)


In [3]:
@btime $x.x500;  ## Slower

  10.862 ns (0 allocations: 0 bytes)


## When working with data DataFrame use barrier functions or type annotation

In [4]:
function f_bad() ## this function will be slow
    Random.seed!(1)
    x = DataFrame(rand(1000000, 2), :auto)
    y, z = x[!, 1], x[!, 2]
    p = 0.0
    for i in 1:nrow(x)
        p += y[i] * z[i]
    end
    p
end

@btime f_bad();
# if you run @code_warntype f_bad() then you notice
# that Julia does not know column types of `DataFrame`

  97.197 ms (5999012 allocations: 122.06 MiB)


solution 1 is to use barrier function (it should be possible to use it in almost any code) for the calculation. You will notice much less memopry allocations and faster performance.

In [5]:
function f_inner(y, z)
    p = 0.0
    for i in eachindex(y, z)
        p += y[i] * z[i]
    end
    p
end

function f_barrier()
    Random.seed!(1)
    x = DataFrame(rand(1000000, 2), :auto)
    f_inner(x[!, 1], x[!, 2])
end

@btime f_barrier();

  4.133 ms (34 allocations: 30.52 MiB)


or use inbuilt function if possible

In [6]:
using LinearAlgebra

function f_inbuilt()
    Random.seed!(1)
    x = DataFrame(rand(1000000, 2), :auto)
    dot(x[!, 1], x[!, 2])
end

@btime f_inbuilt();

  3.480 ms (34 allocations: 30.52 MiB)


solution 2 is to provide the types of extracted columns. However, there are cases in which you will not know these types.

In [7]:
function f_typed()
    Random.seed!(1)
    x = DataFrame(rand(1000000, 2), :auto)
    y::Vector{Float64}, z::Vector{Float64} = x[!, 1], x[!, 2]
    p = 0.0
    for i in 1:nrow(x)
        p += y[i] * z[i]
    end
    p
end

@btime f_typed();

  4.135 ms (34 allocations: 30.52 MiB)


In general for tall and narrow tables it is often useful to use `Tables.rowtable`, `Tables.columntable` or `Tables.namedtupleiterator` for intermediate processing of data in a type-stable way.

## Consider using delayed `DataFrame` creation technique
also notice the difference in performance between copying vs non-copying data frame creation

In [8]:
function f1()
    x = DataFrame([Vector{Float64}(undef, 10^4) for i in 1:100], :auto, copycols=false) ## we work with a DataFrame directly
    for c in 1:ncol(x)
        d = x[!, c]
        for r in 1:nrow(x)
            d[r] = rand()
        end
    end
    x
end

function f1a()
    x = DataFrame([Vector{Float64}(undef, 10^4) for i in 1:100], :auto) ## we work with a DataFrame directly
    for c in 1:ncol(x)
        d = x[!, c]
        for r in 1:nrow(x)
            d[r] = rand()
        end
    end
    x
end

function f2()
    x = Vector{Any}(undef, 100)
    for c in 1:length(x)
        d = Vector{Float64}(undef, 10^4)
        for r in eachindex(d)
            d[r] = rand()
        end
        x[c] = d
    end
    DataFrame(x, :auto, copycols=false) ## we delay creation of DataFrame after we have our job done
end

function f2a()
    x = Vector{Any}(undef, 100)
    for c in eachindex(x)
        d = Vector{Float64}(undef, 10^4)
        for r in eachindex(d)
            d[r] = rand()
        end
        x[c] = d
    end
    DataFrame(x, :auto) ## we delay creation of DataFrame after we have our job done
end

@btime f1();
@btime f1a();
@btime f2();
@btime f2a();

  26.771 ms (1949524 allocations: 37.40 MiB)
  27.464 ms (1949724 allocations: 45.03 MiB)
  1.185 ms (524 allocations: 7.66 MiB)
  1.585 ms (724 allocations: 15.29 MiB)


## You can add rows to a DataFrame in place and it is fast

In [9]:
x = DataFrame(rand(10^6, 5), :auto)
y = DataFrame(transpose(1.0:5.0), :auto)
z = [1.0:5.0;]

@btime vcat($x, $y); ## creates a new DataFrame - slow
@btime append!($x, $y); ## in place - fast

x = DataFrame(rand(10^6, 5), :auto) ## reset to the same starting point
@btime push!($x, $z); ## add a single row in place - fast

  1.701 ms (211 allocations: 38.16 MiB)
  1.425 μs (30 allocations: 1.80 KiB)
  480.281 ns (16 allocations: 256 bytes)


## Allowing missing as well as categorical slows down computations

In [10]:
using StatsBase

function test(data) ## uses countmap function to test performance
    println(eltype(data))
    x = rand(data, 10^6)
    y = categorical(x)
    println(" raw:")
    @btime countmap($x)
    println(" categorical:")
    @btime countmap($y)
    nothing
end

test(1:10)
test([randstring() for i in 1:10])
test(allowmissing(1:10))
test(allowmissing([randstring() for i in 1:10]))

Int64
 raw:
  1.618 ms (7 allocations: 7.63 MiB)
 categorical:
  10.035 ms (4 allocations: 688 bytes)
String
 raw:
  26.519 ms (4 allocations: 528 bytes)
 categorical:
  31.321 ms (4 allocations: 688 bytes)
Union{Missing, Int64}
 raw:
  6.310 ms (4 allocations: 560 bytes)
 categorical:
  15.702 ms (1000004 allocations: 30.52 MiB)
Union{Missing, String}
 raw:
  19.843 ms (4 allocations: 528 bytes)
 categorical:
  31.528 ms (1000004 allocations: 30.52 MiB)


## When aggregating use column selector and prefer integer, categorical, or pooled array grouping variable

In [11]:
df = DataFrame(x=rand('a':'d', 10^7), y=1);

In [12]:
gdf = groupby(df, :x)

GroupedDataFrame with 4 groups based on key: x
First Group (2497251 rows): x = 'b': ASCII/Unicode U+0062 (category Ll: Letter, lowercase)
     Row │ x     y     
         │ Char  Int64 
─────────┼─────────────
       1 │ b         1
       2 │ b         1
    ⋮    │  ⋮      ⋮
 2497250 │ b         1
 2497251 │ b         1
   2497247 rows omitted
⋮
Last Group (2500643 rows): x = 'c': ASCII/Unicode U+0063 (category Ll: Letter, lowercase)
     Row │ x     y     
         │ Char  Int64 
─────────┼─────────────
       1 │ c         1
       2 │ c         1
    ⋮    │  ⋮      ⋮
 2500643 │ c         1
   2500640 rows omitted

traditional syntax, slow

In [13]:
@btime combine(v -> sum(v.y), $gdf)

  18.568 ms (305 allocations: 19.07 MiB)


4×2 DataFrame
 Row │ x     x1      
     │ Char  Int64   
─────┼───────────────
   1 │ b     2497251
   2 │ a     2501619
   3 │ d     2500487
   4 │ c     2500643

use column selector

In [14]:
@btime combine($gdf, :y => sum)

  6.754 ms (186 allocations: 11.45 KiB)


4×2 DataFrame
 Row │ x     y_sum   
     │ Char  Int64   
─────┼───────────────
   1 │ b     2497251
   2 │ a     2501619
   3 │ d     2500487
   4 │ c     2500643

In [15]:
transform!(df, :x => categorical => :x);
gdf = groupby(df, :x)

GroupedDataFrame with 4 groups based on key: x
First Group (2501619 rows): x = CategoricalArrays.CategoricalValue{Char, UInt32} 'a'
     Row │ x     y     
         │ Cat…  Int64 
─────────┼─────────────
       1 │ a         1
       2 │ a         1
    ⋮    │  ⋮      ⋮
 2501618 │ a         1
 2501619 │ a         1
   2501615 rows omitted
⋮
Last Group (2500487 rows): x = CategoricalArrays.CategoricalValue{Char, UInt32} 'd'
     Row │ x     y     
         │ Cat…  Int64 
─────────┼─────────────
       1 │ d         1
       2 │ d         1
    ⋮    │  ⋮      ⋮
 2500487 │ d         1
   2500484 rows omitted

In [16]:
@btime combine($gdf, :y => sum)

  6.805 ms (193 allocations: 12.03 KiB)


4×2 DataFrame
 Row │ x     y_sum   
     │ Cat…  Int64   
─────┼───────────────
   1 │ a     2501619
   2 │ b     2497251
   3 │ c     2500643
   4 │ d     2500487

In [17]:
transform!(df, :x => PooledArray{Char} => :x)

10000000×2 DataFrame
      Row │ x     y     
          │ Char  Int64 
──────────┼─────────────
        1 │ b         1
        2 │ a         1
        3 │ a         1
        4 │ b         1
        5 │ d         1
        6 │ d         1
        7 │ d         1
        8 │ b         1
    ⋮     │  ⋮      ⋮
  9999994 │ c         1
  9999995 │ b         1
  9999996 │ c         1
  9999997 │ a         1
  9999998 │ d         1
  9999999 │ d         1
 10000000 │ b         1
    9999985 rows omitted

In [18]:
gdf = groupby(df, :x)

GroupedDataFrame with 4 groups based on key: x
First Group (2497251 rows): x = 'b': ASCII/Unicode U+0062 (category Ll: Letter, lowercase)
     Row │ x     y     
         │ Char  Int64 
─────────┼─────────────
       1 │ b         1
       2 │ b         1
    ⋮    │  ⋮      ⋮
 2497250 │ b         1
 2497251 │ b         1
   2497247 rows omitted
⋮
Last Group (2500643 rows): x = 'c': ASCII/Unicode U+0063 (category Ll: Letter, lowercase)
     Row │ x     y     
         │ Char  Int64 
─────────┼─────────────
       1 │ c         1
       2 │ c         1
    ⋮    │  ⋮      ⋮
 2500643 │ c         1
   2500640 rows omitted

In [19]:
@btime combine($gdf, :y => sum)

  6.745 ms (188 allocations: 11.52 KiB)


4×2 DataFrame
 Row │ x     y_sum   
     │ Char  Int64   
─────┼───────────────
   1 │ b     2497251
   2 │ a     2501619
   3 │ d     2500487
   4 │ c     2500643

## Use views instead of materializing a new DataFrame

In [20]:
x = DataFrame(rand(100, 1000), :auto)
@btime $x[1:1, :]

  196.315 μs (2986 allocations: 159.50 KiB)


1×1000 DataFrame
 Row │ x1        x2        x3        x4        x5       x6        x7        x8 ⋯
     │ Float64   Float64   Float64   Float64   Float64  Float64   Float64   Fl ⋯
─────┼──────────────────────────────────────────────────────────────────────────
   1 │ 0.521901  0.692887  0.366414  0.102794  0.19886  0.374543  0.729784  0. ⋯
                                                             993 columns omitted

In [21]:
@btime $x[1, :]

  19.433 ns (0 allocations: 0 bytes)


DataFrameRow
 Row │ x1        x2        x3        x4        x5       x6        x7        x8 ⋯
     │ Float64   Float64   Float64   Float64   Float64  Float64   Float64   Fl ⋯
─────┼──────────────────────────────────────────────────────────────────────────
   1 │ 0.521901  0.692887  0.366414  0.102794  0.19886  0.374543  0.729784  0. ⋯
                                                             993 columns omitted

In [22]:
@btime view($x, 1:1, :)

  19.433 ns (0 allocations: 0 bytes)


1×1000 SubDataFrame
 Row │ x1        x2        x3        x4        x5       x6        x7        x8 ⋯
     │ Float64   Float64   Float64   Float64   Float64  Float64   Float64   Fl ⋯
─────┼──────────────────────────────────────────────────────────────────────────
   1 │ 0.521901  0.692887  0.366414  0.102794  0.19886  0.374543  0.729784  0. ⋯
                                                             993 columns omitted

In [23]:
@btime $x[1:1, 1:20]

  4.414 μs (51 allocations: 4.28 KiB)


1×20 DataFrame
 Row │ x1        x2        x3        x4        x5       x6        x7        x8 ⋯
     │ Float64   Float64   Float64   Float64   Float64  Float64   Float64   Fl ⋯
─────┼──────────────────────────────────────────────────────────────────────────
   1 │ 0.521901  0.692887  0.366414  0.102794  0.19886  0.374543  0.729784  0. ⋯
                                                              13 columns omitted

In [24]:
@btime $x[1, 1:20]

  21.284 ns (0 allocations: 0 bytes)


DataFrameRow
 Row │ x1        x2        x3        x4        x5       x6        x7        x8 ⋯
     │ Float64   Float64   Float64   Float64   Float64  Float64   Float64   Fl ⋯
─────┼──────────────────────────────────────────────────────────────────────────
   1 │ 0.521901  0.692887  0.366414  0.102794  0.19886  0.374543  0.729784  0. ⋯
                                                              13 columns omitted

In [25]:
@btime view($x, 1:1, 1:20)

  20.047 ns (0 allocations: 0 bytes)


1×20 SubDataFrame
 Row │ x1        x2        x3        x4        x5       x6        x7        x8 ⋯
     │ Float64   Float64   Float64   Float64   Float64  Float64   Float64   Fl ⋯
─────┼──────────────────────────────────────────────────────────────────────────
   1 │ 0.521901  0.692887  0.366414  0.102794  0.19886  0.374543  0.729784  0. ⋯
                                                              13 columns omitted

---

*This notebook was generated using [Literate.jl](https://github.com/fredrikekre/Literate.jl).*